# RUN experiments

In this notebook, we will run all the required experiments using the `Experiment` class, which can be found at `sscode/experiment.py`, and can be seen below:

```python
    class Experiment(object):
        """
        This class Experiment summarizes all the previous work done with the linear and the
        knn models, as this class allows the user to perform a detailed analysis of one
        requested model given a set of parameters

        """

        def __init__(self, slp_data, wind_data, ss_data, # this must have several stations
                     sites_to_analyze: list = list(np.random.randint(10,1000,5)),
                     model: str = 'linear', # this is the model to analyze
                     model_metrics: list = [
                         'bias','si','rmse','pearson','spearman','rscore',
                         'mae', 'me', 'expl_var', # ...
                     ], # these are the metrics to evaluate
                     pca_attrs: dict = pca_attrs_default,
                     model_attrs: dict = linear_attrs_default):
            """
            As the initializator, the __init__ funciton creates the instance of the class,
            given a set of parameters, which are described below

            Args:
                slp_data (xarray.Dataset): These are the sea-level-pressure fields, previously
                    loaded with the Loader class, loader.predictor_slp!!
                wind_data (xarray.Dataset): These are the wind fields, previously
                    loaded with the Loader class, loader.predictor_wind!!
                ss_data (xarray.Dataset): This is the storm surge from the moana hindcast, previously
                    loaded with the Loader class, loader.predictand!!
                sites_to_analyze (list, optional): This is the list with all the moana v2
                    hindcast locations to analyze. Defaults to random locations.
                model (str, optional): Type of model to analyze. Defaults to 'linear'.
                model_metrics (list, optional): These are all the evaluation metrics that might
                    be used to evaluate the model performance. Defaults to simple list.
                pca_attrs (dict, optional): PCA dictionary with all the parameters to use.
                    Defaults to pca_attrs_default.
                model_attrs (dict, optional): Model dictionary with all the parameters to use. 
                    Defaults to linear_attrs_default.
            """

            # lets build the experiment!!
```

where it can be seen how, given the sea-level-pressure / wind data, the storm surge (it is preferable to use the Moana v2 hindcast nearshore), all the individual sites to analyze, the type of model that will be used (with its evaluation metrics), and the PCA attributes and the MODEL attributes that will be used to calculate the model.

Given these parameters, we construct the object of the class, and then running `execute_cross_model_calculations`, we can perform all the experiments given the possible combinations!!

```{warning}
Be careful with the ["curse of dimensionality"](https://en.wikipedia.org/wiki/Curse_of_dimensionality), as it seems very easy to add more options for the parameters of the models, but once we have more than 3-4 parameters with 2-3 different values, the number of models that will be performed can increase to hundreds!!
```

Below, different code cells with imports, loading functions, visualizations... will appear, but thw worflow is similar to all the notebooks in the repository. Once we load the data, we use the pre-built python classes to generate results!!

In [1]:
# basics
import os, sys

# arrays
import numpy as np
import xarray as xr

# append sscode to path
sys.path.insert(0, '..')
# data_path = '/data' #'/data/storm_surge_data/'
# os.environ["SSURGE_DATA_PATH"] = data_path

# custom
from sscode.config import default_location, \
    default_region, default_region_reduced, default_evaluation_metrics
from sscode.data import Loader
from sscode.experiment_new import Experiment

# warnings
import warnings
warnings.filterwarnings('ignore')

# for autocomplete code
%config Completer.use_jedi = False

DATA PATH /home/javitausia/Documentos/geocean-nz-ss/data


## Load the data, SLP and SS

Below, we load the slp fields and the Moana v2 hindcast data nearshore. Have three things in mind:

* First, the winds are **NOT** loaded, as we prefer to calculate the gradient of the slp fields. Having in mind that winds have more resolution (more computation is required) and the fact that we are playing around with projected winds, adds this new calculation to each step (and the Loader class is calculated outside the class Experiment, so the projedted winds are calculated just to one location).

* The `plot` parameter is set to `False`, but can be set to `True` if all the plots are wanted to be seen.

* The Moana v2 hindcast nearshore is used, and although the gridded netCDF data can be used, which includes ss data all over the New Zealand region, the data might be transformed to `dim=site` inside the dataset, as we did in previous notebooks.

In [2]:
# load the data
load_cfsr_moana_uhslc = Loader(
    data_to_load=['cfsr','moana','uhslc'], plot=False, 
    time_resample='1D', load_winds=True
)


 loading the sea-level-pressure fields... 


 loading daily resampled data... 


 loading and plotting the UHSLC tidal guages... 



## Create / Run -- Experiment object

In the two cells below, we first choose all the values that will have the different parameters for the model that will be used, and then we create the instance of the class `Experiment`, where different logs will appear before running all the models.

In [3]:
# experiment attributes
# ---------------------

sites_to_analyze = np.unique( # closest Moana v2 Hindcast to tidal gauges
    [ 689,328,393,1327,393,480,999,116,224,1124,949,708, # UHSLC
      1296,378,1124,780,613,488,1442,1217,578,200,1177,1025,689,949,224,1146, # LINZ
      1174,1260,1217,744,1064,1214,803,999 # OTHER (ports...)
    ]
)
sites_to_analyze = np.arange(
    len(load_cfsr_moana_uhslc.predictand.site.values)
)[::5]

pca_attrs_exp = {
    'calculate_gradient': [True],
    'winds': [True],
    'time_lapse': [3], # 1 equals to NO time delay 
    'time_resample': ['1D'], # 6H and 12H available...
    'region': [('local',(2.5,2.5))]
}
linear_attrs_exp = {
    'train_size': [0.7], 'percentage_PCs': [0.98]
}
knn_attrs_exp = {
    'train_size': [0.7], 'percentage_PCs': [0.98],
    'k_neighbors': np.arange(1,50,1) # None calculates the optimum k-neighs
}
xgboost_attrs_exp = {
    'train_size': [0.7], 'percentage_PCs': [0.98],
    'n_estimators': [50], 'max_depth': [10,12],
    'min_samples_split': [0.04,0.06],
    'learning_rate': [0.1], 'loss': ['ls'] # more could be added
}

```{note}
Please check `Experiment` logs before running `execute_cross_model_calculations()`!!
```

In [4]:
# create the experiment
experiment = Experiment(
    load_cfsr_moana_uhslc.predictor_slp, 
    load_cfsr_moana_uhslc.predictor_wind,
    load_cfsr_moana_uhslc.predictand, # all the sites are passed to exp at first
    sites_to_analyze=sites_to_analyze, 
    model='knn', # model that will be used to predict
    model_metrics=default_evaluation_metrics,
    pca_attrs=pca_attrs_exp,
    model_attrs=knn_attrs_exp
)


 The model has been correctly initialized with || model = knn ||             

 and model evaluation metrics = ['bias', 'si', 'rmse', 'rel_rmse', 'pearson', 'rscore', 'ext_rmse', 'ext_rel_rmse', 'ext_pearson', 'pocid', 'tu_test', 'expl_var', 'nse', 'kge', 'kgeprime', 'ext_nse', 'ext_kge', 'ext_kgeprime']             

 pca_params = {'calculate_gradient': [True], 'winds': [True], 'time_lapse': [3], 'time_resample': ['1D'], 'region': [('local', (2.5, 2.5))]} 

 model_params = {'train_size': [0.7], 'percentage_PCs': [0.98], 'k_neighbors': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34,
       35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49])}             

 which makes a total of 49 iterations as there are (1, 1, 1, 1, 1, 1, 1, 49) values for each parameter             

 the experiment will be performed in sites = [   0    5   10   15   20   25   30   35   40   45   50   55  

```{note}
Once the instance of the class is well created, lets run all the models running the cell below
```

In [ ]:
# run all the models
exp_parameters, exp_mean_parameters, final_stats = experiment.execute_cross_model_calculations(
    verbose=True, plot=False # plot logs when computing the models
)


 ---------------------------------------------------------                         

 Experiment 1 in site 0 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 1}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 0)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', 'None', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/geocean-nz-ss/data/pcs/local_2.5_-2.5_None_winds_gradients_1D_tl3.nc
PCs loaded from file

 14 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 1 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.73, Relative - RMSE: 0.39
 and Correlations (Pearson, Rscore): (0.66, 0.37)
 NSE = [0.3704


 14 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 8 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.56, Relative - RMSE: 0.29
 and Correlations (Pearson, Rscore): (0.80, 0.64)
 NSE = [0.63794442], KGE = [0.6566963] and KGE_PRIME = [0.6742915]
 R score: 0.64 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 9 in site 0 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 9}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 8)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', 'None', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/geocea


 14 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 16 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.54, Relative - RMSE: 0.29
 and Correlations (Pearson, Rscore): (0.82, 0.66)
 NSE = [0.65584575], KGE = [0.63481134] and KGE_PRIME = [0.65734868]
 R score: 0.66 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 17 in site 0 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 17}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 16)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', 'None', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/


 14 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 24 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.54, Relative - RMSE: 0.29
 and Correlations (Pearson, Rscore): (0.83, 0.66)
 NSE = [0.65731377], KGE = [0.61864356] and KGE_PRIME = [0.64866478]
 R score: 0.66 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 25 in site 0 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 25}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 24)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', 'None', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/


 14 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 32 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.54, Relative - RMSE: 0.29
 and Correlations (Pearson, Rscore): (0.83, 0.66)
 NSE = [0.65713682], KGE = [0.60664681] and KGE_PRIME = [0.63691169]
 R score: 0.66 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 33 in site 0 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 33}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 32)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', 'None', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/

...


 27 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 20 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.57, Relative - RMSE: 0.30
 and Correlations (Pearson, Rscore): (0.80, 0.62)
 NSE = [0.62224225], KGE = [0.5822738] and KGE_PRIME = [0.66403595]
 R score: 0.62 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 21 in site 660 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 21}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 20)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', '660', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/


 27 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 28 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.57, Relative - RMSE: 0.30
 and Correlations (Pearson, Rscore): (0.81, 0.62)
 NSE = [0.61841365], KGE = [0.56560186] and KGE_PRIME = [0.65267496]
 R score: 0.62 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 29 in site 660 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 29}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 28)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', '660', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos


 27 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 36 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.58, Relative - RMSE: 0.30
 and Correlations (Pearson, Rscore): (0.81, 0.62)
 NSE = [0.61500076], KGE = [0.55312712] and KGE_PRIME = [0.64449672]
 R score: 0.62 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 37 in site 660 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 37}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 36)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', '660', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos


 27 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 44 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.58, Relative - RMSE: 0.31
 and Correlations (Pearson, Rscore): (0.81, 0.61)
 NSE = [0.60987895], KGE = [0.54129114] and KGE_PRIME = [0.63654645]
 R score: 0.61 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 45 in site 660 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 45}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 44)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', '660', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos


 22 PCs (0.98 expl. variance) will be used to train the model!! 


 KNN regression with 3 neighbors... 

Data comparison is   --   BIAS: 0.00, SI: 0.58, Relative - RMSE: 0.29
 and Correlations (Pearson, Rscore): (0.79, 0.62)
 NSE = [0.61893673], KGE = [0.71514066] and KGE_PRIME = [0.72661446]
 R score: 0.62 -- in TEST data

 ---------------------------------------------------------                         

 Experiment 4 in site 665 ......                         

 pca_params = {'calculate_gradient': True, 'winds': True, 'time_lapse': 3, 'time_resample': '1D', 'region': ('local', (2.5, 2.5))} 

 knn_model_params = {'train_size': 0.7, 'percentage_PCs': 0.98, 'k_neighbors': 4}                         

 and iteration with indexes = (0, 0, 0, 0, 0, 0, 0, 3)                         

time resample 1D------------------------------------------
/home/javitausia/Documentos/geocean-nz-ss/data/pcs ['local_2.5_-2.5', '665', 'winds', 'gradients', '1D', 'tl3']
FILE /home/javitausia/Documentos/geo

In [ ]:
print("Done")

In [ ]:
# finally, we can save the results, using the following function
def save_final_results(to_save_name: str = 
    '../data/statistics/experiments/experiment_linear_final.nc'):
    
    """
        This function saves the results in netCDF4 format
    """
    
    sites_datasets = [] # save all xarray.Dataset's in sites
    for site,exp_metrics_site in zip(experiment.ss_sites,exp_parameters):
        site_metrics = {}
        for im,metric in enumerate(final_stats):
            site_metrics[metric] = (
                ('grad','winds','tlapse','tresample','region','tsize','perpcs'),
                exp_metrics_site[:,:,:,:,:,:,:,im])
        sites_datasets.append(xr.Dataset(site_metrics).expand_dims(
            {'site':[site]}
        ))
    experiment_metrics = xr.concat(sites_datasets,dim='site')
    # experiment_metrics.to_netcdf(to_save_name)
    
    return experiment_metrics

In [ ]:
# save_final_results('../data/statistics/experiments/jeje.nc')

In [ ]:
# finally, we can save the results, using the following function
def save_final_results_knn(to_save_name: str = 
    '../data/statistics/experiments/experiment_linear_final.nc'):
    
    """
        This function saves the results in netCDF4 format
    """
    
    sites_datasets = [] # save all xarray.Dataset's in sites
    for site,exp_metrics_site in zip(experiment.ss_sites,exp_parameters):
        site_metrics = {}
        for im,metric in enumerate(final_stats):
            site_metrics[metric] = (
                ('grad','winds','tlapse','tresample','region','tsize','perpcs', 'k_neighbors'),
                exp_metrics_site[:,:,:,:,:,:,:,:,im]) 
        sites_datasets.append(xr.Dataset(site_metrics).expand_dims(
            {'site':[site]}
        ))
    experiment_metrics = xr.concat(sites_datasets,dim='site')
    experiment_metrics.to_netcdf(to_save_name)
    
    return experiment_metrics

In [ ]:
save_final_results_knn('../data/statistics/experiments/test_knn_ext.nc')